# FINAL PROJECT TLCN - CHATBOT HỖ TRỢ TRA CỨU THÔNG TIN SỨC KHỎE
- Author:
  - Đặng Kim Thành - 21110298
  - Bùi Quốc Khang - 21110202
## Phần 1 - MeDiChat ViVi - Retrieval-Augmented Generation Normal

### I. Xử lý dữ liệu

#### Import môi trường cơ sở dữ liệu và thư viện

In [1]:
import os
os.environ['PINECONE_API_KEY'] = "4a66e93f-c567-496a-a39c-546ec74c344d"
pinecone_api_key = os.getenv('PINECONE_API_KEY')
pinecone_api_key

'4a66e93f-c567-496a-a39c-546ec74c344d'

In [2]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.document_loaders import PyPDFLoader, DirectoryLoader, TextLoader
from pinecone import Pinecone
from langchain_pinecone import PineconeVectorStore
import unidecode
import re
import pdfplumber
import json

c:\Users\ADMIN\OneDrive\Documents\Btap_Code\VisualStudioCode\Python\TLCN_HealthChatbot\.venv\Lib\site-packages\pinecone\data\index.py:1: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


#### Tải dữ liệu gốc từ file PDF (không có xử lý)

In [6]:
def read_pdfs_from_directory(directory_path):
    """
    Đọc nội dung từ tất cả các tệp PDF trong một thư mục.

    Args:
        directory_path (str): Đường dẫn đến thư mục chứa các tệp PDF.

    Returns:
        dict: Từ điển chứa tên tệp PDF và nội dung tương ứng.
    """
    pdf_contents = {}

    # Kiểm tra thư mục tồn tại
    if not os.path.exists(directory_path):
        raise FileNotFoundError(f"Thư mục không tồn tại: {directory_path}")

    # Lặp qua tất cả các tệp trong thư mục
    for file_name in os.listdir(directory_path):
        file_path = os.path.join(directory_path, file_name)

        # Kiểm tra xem tệp có phải là PDF không
        if os.path.isfile(file_path) and file_name.lower().endswith('.pdf'):
            try:
                # Đọc nội dung từ tệp PDF bằng pdfplumber
                with pdfplumber.open(file_path) as pdf:
                    content = ""
                    for page in pdf.pages:
                        content += page.extract_text() + "\n"

                # Thêm nội dung vào từ điển
                pdf_contents[file_name] = content

            except Exception as e:
                print(f"Lỗi khi đọc tệp {file_name}: {e}")

    return pdf_contents

In [4]:
folder_path = 'data/PDF'  # Đường dẫn tới thư mục chứa các tệp cần đổi tên

In [7]:
documents = read_pdfs_from_directory(folder_path)

In [6]:
documents

{'co_che_trieu_chung_hoc.pdf': "Cơ Chế\nTriệu Chứng Học\n\nCơ Chế\nTriệu Chứng Học\nBiên Dịch: Nhóm Chia Sẻ Ca Lâm Sàng\nFacebook: https://www.facebook.com/calamsanghay/\nMark Dennis\nGiám Đốc Bệnh ViệnWollongong, Australia\nWilliam Talbot Bowen\nTrưởng Khoa Cấp Cứu\nBệnh Viện Đại Học Y Khoa\nBang Louisiana, Hoa Kì\nLucy Cho\nGiám Đốc Bệnh Viện Hoàng Gia Newcastle, Úc\nMục Lục\nChương 1 Nghiệm pháp Thomas. . . . . . . . . . .54\nTriệu Chứng Cơ Xương Khớp . . . . . .1 Nghiệm pháp Tinel. . . . .. . . . . . . . . . . . . .55\nDấu hiệu Trendelenburg. . . .. . . . . . . . . . .56\nDấu hiệu ngăn kéo trước . . . . . . . . ..2\nSự khác biệt độ dài 2 chân thực sự. . . . . .57\nNghiệm pháp Apley. . . . . . . . . . . . .3\nBàn tay gió thổi . . . . . . . . . . . . . 58\nNghiệm pháp cào lưng Apley. . . . . . . . . 4\nDấu hiệu chữ V . . . . . . . . . . . . . 59\nBất bình đẳng chiều dài. . . . . . . . . . . 5\nVẹo ngoài. . . . . . . . . . . . . . . .60\nNghiệm pháp e sợ. . . . . . . . . .. .. . . . .

#### Tải dữ liệu PDF có xử lý

In [9]:
folder_path = 'data/PDF'  # Đường dẫn tới thư mục chứa các tệp cần đổi tên

-   Xử lý tên file (trách bị lỗi khi tải dữ liệu)

In [10]:
# Duyệt qua tất cả các tệp trong thư mục
for filename in os.listdir(folder_path):
    # Chuyển đổi tên tệp sang không dấu
    new_filename = unidecode.unidecode(filename)
    # Thay thế dấu cách bằng dấu gạch dưới
    new_filename = new_filename.replace(' ', '_')
    # Loại bỏ các ký tự đặc biệt, chỉ giữ lại chữ cái, số và dấu gạch dưới
    new_filename = re.sub(r'[^A-Za-z0-9_.]', '', new_filename)

    # Đổi tên tệp
    os.rename(os.path.join(folder_path, filename), os.path.join(folder_path, new_filename))
    print(f"Đã đổi tên tệp: {filename} -> {new_filename}")

Đã đổi tên tệp: co_che_trieu_chung_hoc.pdf -> co_che_trieu_chung_hoc.pdf


#### Chuẩn hóa dữ liệu từ PDF thành TXT

In [ ]:
def normalize_filename(filename):
    filename = unidecode.unidecode(filename)
    filename = filename.replace(" ", "_")
    return filename

def remove_page_numbers(text):
    # Loại bỏ số trang chỉ là một con số ở cuối dòng
    lines = text.splitlines()
    cleaned_lines = []
    for line in lines:
        # Nếu dòng chỉ có một con số ở cuối, bỏ nó đi
        if re.match(r'^\s*\d+\s*$', line.strip()):
            continue
        cleaned_lines.append(line)
    return "\n".join(cleaned_lines)

def pdf_to_text(pdf_file, txt_file):
    with pdfplumber.open(pdf_file) as pdf:
        text = ""
        for page_num, page in enumerate(pdf.pages):
            # Trích xuất văn bản từ trang
            page_text = page.extract_text()
            
            # Trích xuất và xử lý bảng
            tables = page.extract_tables()
            for table in tables:
                for row in table:
                    row_text = "\t".join([cell if cell is not None else "" for cell in row])
                    page_text += "\n" + row_text
            
            # Thêm văn bản của trang vào text
            text += page_text + "\n"
    
    # Loại bỏ số trang khỏi văn bản
    cleaned_text = remove_page_numbers(text)

    # Ghi toàn bộ nội dung đã được làm sạch vào file txt
    with open(txt_file, 'w', encoding='utf-8') as txt:
        txt.write(cleaned_text)

def convert_pdfs_in_folder(pdf_path, txt_path):
    os.makedirs(txt_path, exist_ok=True)
    for filename in os.listdir(pdf_path):
        if filename.endswith('.pdf'):
            nomalized_filename = normalize_filename(filename)
            pdf_file = os.path.join(pdf_path, filename)
            txt_file = os.path.join(txt_path, nomalized_filename.replace('.pdf', '.txt'))
            pdf_to_text(pdf_file, txt_file)
            print(f'Đã chuyển đổi {pdf_file} thành {txt_file}')

In [12]:
pdf_path = 'data/PDF'
txt_path = 'data/TXT'
convert_pdfs_in_folder(pdf_path, txt_path)

Đã chuyển đổi data/PDF\co_che_trieu_chung_hoc.pdf thành data/TXT\co_che_trieu_chung_hoc.txt


#### Xử lý sâu vào dữ liệu txt

In [19]:
def clean_text_line(line):
    # Xóa các khoảng trắng đầu/cuối dòng và các ký tự không cần thiết
    line = line.strip()
    line = re.sub(r'\s+', ' ', line)  # Thay nhiều khoảng trắng bằng một khoảng trắng
    return line

def clean_table_data(lines):
    cleaned_data = []
    for line in lines:
        cleaned_line = clean_text_line(line)
        if cleaned_line:  # Bỏ qua dòng trống
            # Tách dữ liệu theo các dấu tab hoặc khoảng trắng lớn
            cleaned_data.append(cleaned_line.replace('\t', ', ').replace('  ', ', '))
    return cleaned_data

def clean_and_merge_lines(lines):
    merged_lines = []
    buffer = ""

    for line in lines:
        stripped_line = line.strip()
        
        # Nếu buffer đang chứa một đoạn văn, nối nó với dòng tiếp theo nếu cần
        if buffer:
            if stripped_line and not stripped_line[0].isupper():
                buffer += " " + stripped_line
            else:
                merged_lines.append(buffer)
                buffer = stripped_line
        else:
            buffer = stripped_line

    # Thêm dòng cuối cùng còn lại trong buffer nếu có
    if buffer:
        merged_lines.append(buffer)
    
    return merged_lines

#### Hàm lưu file

In [20]:
def save_cleaned_data(cleaned_data, output_file):
    with open(output_file, 'w', encoding='utf-8') as f:
        for line in cleaned_data:
            f.write(line + '\n')

def process_txt_file(txt_file, cleaned_txt_file):
    with open(txt_file, 'r', encoding='utf-8') as f:
        lines = f.readlines()

    merged_lines = clean_and_merge_lines(lines)
    cleaned_data = clean_table_data(merged_lines)
    
    save_cleaned_data(cleaned_data, cleaned_txt_file)

def process_all_files_in_folder(input_folder, output_folder):
    # Tạo thư mục đích nếu chưa tồn tại
    os.makedirs(output_folder, exist_ok=True)
    
    for filename in os.listdir(input_folder):
        if filename.endswith('.txt'):
            input_file = os.path.join(input_folder, filename)
            output_file = os.path.join(output_folder, filename)
            process_txt_file(input_file, output_file)
            print(f'Đã xử lý {input_file} và lưu vào {output_file}')

In [21]:
input_folder = 'data/TXT'
output_folder = 'data/cleaned_txt_files'

process_all_files_in_folder(input_folder, output_folder)

Đã xử lý data/TXT\co_che_trieu_chung_hoc.txt và lưu vào data/cleaned_txt_files\co_che_trieu_chung_hoc.txt


#### Phương pháp xử lý dữ liệu đầu vào bằng OCR 

In [1]:
import aspose.ocr as ocr

settings = ocr.RecognitionSettings()
print(dir(settings))  # In ra các thuộc tính và phương thức của đối tượng settings
print(dir(ocr.Language))
print(dir(ocr.InputType))


['__class__', '__delattr__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '_aspose_clr_castable_obj', '_aspose_clr_host', '_cast_as', '_cast_from', '_cast_to', '_is_assignable', '_reinterpret_obj', '_type_of', 'allowed_characters', 'allowed_symbols', 'automatic_color_inversion', 'detect_areas_mode', 'get_type', 'ignored_symbols', 'language', 'lines_filtration', 'recognition_areas', 'recognize_single_line', 'threads_count', 'upscale_small_font']
['AFR', 'ALN', 'ARA', 'AWA', 'AZB', 'BCL', 'BEL', 'BEM', 'BEW', 'BGC', 'BHO', 'BHR', 'BJJ', 'BOS', 'BUL', 'CAT', 'CCX', 'CDO', 'CEB', 'CES', 'CHE', 'CHI', 'CMN', 'CPX', 'CYRILLIC', 'CZE', 'DAN', 'DEU', 'DHD', 'DIQ', 'DOC', 'DUM', 'ENG', 'EST', 'EXT_LATIN', 'FIN', 'FRA', 'GAN', 'GAX', 'GBM', 'GLG', 'GLK', 'GUZ', 'HAK', '

In [ ]:
import fitz  # PyMuPDF
import numpy as np
import cv2
import aspose.ocr as ocr
import os

# Đường dẫn đến thư mục chứa các file PDF và TXT
pdf_directory = "data\PDF"
txt_directory = "data\OCR"

# Khởi tạo công cụ OCR
api = ocr.AsposeOcr()

# Cài đặt nhận dạng
settings = ocr.RecognitionSettings()
settings.automatic_color_inversion = True

# Duyệt qua từng file PDF trong thư mục
for filename in os.listdir(pdf_directory):
    if filename.endswith(".pdf"):
        pdf_path = os.path.join(pdf_directory, filename)
        doc = fitz.open(pdf_path)

        recognized_text = ""

        # Lặp qua từng trang PDF
        for page_num in range(doc.page_count):
            page = doc.load_page(page_num)
            pix = page.get_pixmap()
            img = np.frombuffer(pix.samples, dtype=np.uint8).reshape(pix.height, pix.width, pix.n)

            # Chuyển đổi sang grayscale và khử nhiễu
            gray_image = cv2.cvtColor(img, cv2.COLOR_RGB2GRAY)
            denoised_image = cv2.fastNlMeansDenoising(gray_image, None, 30, 7, 21)

            # Lưu ảnh tạm thời để OCR và không tự động xóa ngay
            temp_image_path = f"{pdf_directory}/temp_page_{page_num}.png"
            cv2.imwrite(temp_image_path, denoised_image)

            # Nhận diện văn bản từ ảnh đã lưu tạm
            files = ocr.OcrInput(ocr.InputType.SINGLE_IMAGE)
            files.add(temp_image_path)

            result = api.recognize(files, settings)
            recognized_text += result[0].recognition_text + "\n"

            # Xóa file tạm sau khi nhận diện xong
            os.remove(temp_image_path)

        # Lưu kết quả OCR vào file .txt với tên tương ứng
        output_text_path = os.path.join(txt_directory, f"{os.path.splitext(filename)[0]}_out.txt")
        with open(output_text_path, "w", encoding="utf-8") as f:
            f.write(recognized_text)

        print(f"OCR completed for {filename}. Output saved to {output_text_path}")

OCR completed for co_che_trieu_chung_hoc.pdf. Output saved to data\OCR\co_che_trieu_chung_hoc_out.txt


#### Xử lý dữ liệu dạng JSON

- Chuẩn hóa dữ liệu Prompt Vietnamese

In [42]:
def convert_to_prompt_format_vi(disease_data):
  messages = []

  for disease in disease_data["diseases"]:
    l_messages = []
    system_message = {
        "from": "system",
        "value": "Bạn là một trợ lí Tiếng Việt nhiệt tình và trung thực. Hãy luôn trả lời một cách hữu ích nhất có thể, đồng thời giữ an toàn. Nếu một câu hỏi không có ý nghĩa hoặc không hợp lý về mặt thông tin, hãy giải thích tại sao thay vì trả lời một điều gì đó không chính xác, vui lòng không chia sẻ thông tin sai lệch."
    }

    user_message = {
        "from": "human",
        "value": f"Mô tả về bệnh {disease['name']}?"
    }
    assistant_message = {
        "from": "gpt",
        "value": f"Mô tả: {disease['description']}.\n\nTriệu chứng: {', '.join(disease['symptoms'])}."
    }
    l_messages.append(system_message)
    l_messages.append(user_message)
    l_messages.append(assistant_message)
    messages.append(l_messages)

    l_messages = []
    user_message = {
        "from": "human",
        "value": f"Triệu chứng về bệnh {disease['name']}?"
    }
    assistant_message = {
        "from": "gpt",
        "value": f"Triệu chứng: {', '.join(disease['symptoms'])}.\n\nPhương pháp điều trị: {', '.join(disease['treatments'])}."
    }
    l_messages.append(system_message)
    l_messages.append(user_message)
    l_messages.append(assistant_message)
    messages.append(l_messages)

    l_messages = []
    user_message = {
        "from": "human",
        "value": f"Phương pháp chữa bệnh {disease['name']}?"
    }
    assistant_message = {
        "from": "gpt",
        "value": f"Phương pháp điều trị: {', '.join(disease['treatments'])}."
    }
    l_messages.append(system_message)
    l_messages.append(user_message)
    l_messages.append(assistant_message)
    messages.append(l_messages)

  return messages

- Chuẩn hóa dữ liệu Prompt English

In [ ]:
def convert_to_prompt_format_en(disease_data):
    messages = []

    for disease in disease_data["diseases"]:
        # Thiết lập 3 messages để mô tả bệnh
        l_messages = []
        system_message = {
            "from": "system",
            "value": "You are a helpful and honest assistant. Always provide the most useful answers possible, while ensuring safety. If a question is meaningless or unreasonable, explain why instead of providing incorrect information, and please do not share misleading information."
        }
        user_message = {
            "from": "human",
            "value": f"Describe the disease {disease['name']}?"
        }
        assistant_message = {
            "from": "gpt",
            "value": f"Description: {disease['description']}.\n\nSymptoms: {', '.join(disease['symptoms'])}."
        }
        l_messages.append(system_message)
        l_messages.append(user_message)
        l_messages.append(assistant_message)
        messages.append(l_messages)

        # Thiết lập 3 messages cho triệu chứng bệnh
        l_messages = []
        l_messages.append(system_message)
        user_message = {
            "from": "human",
            "value": f"What are the symptoms of the disease {disease['name']}?"
        }
        assistant_message = {
            "from": "gpt",
            "value": f"Symptoms: {', '.join(disease['symptoms'])}.\n\nTreatment methods: {', '.join(disease['treatments'])}."
        }
        l_messages.append(user_message)
        l_messages.append(assistant_message)
        messages.append(l_messages)

        # Thiết lập 3 messages cho cách chữa trị 
        l_messages = []
        l_messages.append(system_message)
        user_message = {
            "from": "human",
            "value": f"What are the treatment methods for the disease {disease['name']}?"
        }
        assistant_message = {
            "from": "gpt",
            "value": f"Treatment methods: {', '.join(disease['treatments'])}."
        }
        l_messages.append(user_message)
        l_messages.append(assistant_message)
        messages.append(l_messages)

    return messages

In [44]:
def read_json_and_convert_to_txt(input_file, output_file, data_type):
    with open(input_file, 'r', encoding='utf-8') as infile:
        disease_data = json.load(infile)

    if data_type == "en":
        messages = convert_to_prompt_format_en(disease_data)
    elif data_type == "vi":
        messages = convert_to_prompt_format_vi(disease_data)

    with open(output_file, 'w', encoding='utf-8') as outfile:
        outfile.write(json.dumps(messages, ensure_ascii=False, indent=2))

In [46]:
# Đọc file JSON và chuyển đổi thành TXT english
input_file = 'data/JSON/health-data-en.json'
output_file = 'data/cleaned_txt_files/health-data-en.txt'
read_json_and_convert_to_txt(input_file, output_file, "en")

In [47]:
# Đọc file JSON và chuyển đổi thành TXT vietnam
input_file = 'data/JSON/health-data-vi.json'
output_file = 'data/cleaned_txt_files/health-data-vi.txt'
read_json_and_convert_to_txt(input_file, output_file, "vi")

### II. Chuẩn hóa dữ liệu thành Document của LangChain

In [48]:
class UTF8TextLoader(TextLoader):
    def __init__(self, file_path):
        super().__init__(file_path, encoding='utf-8')   

pdf_path = 'data/cleaned_txt_files'
loader = DirectoryLoader(path=pdf_path, glob='*.txt', loader_cls=UTF8TextLoader)
documents = loader.load()

In [49]:
documents

[Document(metadata={'source': 'data\\cleaned_txt_files\\co_che_trieu_chung_hoc.txt'}, page_content="Cơ Chế\nTriệu Chứng Học\nCơ Chế\nTriệu Chứng Học\nBiên Dịch: Nhóm Chia Sẻ Ca Lâm Sàng\nFacebook: https://www.facebook.com/calamsanghay/\nMark Dennis\nGiám Đốc Bệnh ViệnWollongong, Australia\nWilliam Talbot Bowen\nTrưởng Khoa Cấp Cứu\nBệnh Viện Đại Học Y Khoa\nBang Louisiana, Hoa Kì\nLucy Cho\nGiám Đốc Bệnh Viện Hoàng Gia Newcastle, Úc\nMục Lục\nChương 1 Nghiệm pháp Thomas. . . . . . . . . . .54\nTriệu Chứng Cơ Xương Khớp . . . . . .1 Nghiệm pháp Tinel. . . . .. . . . . . . . . . . . . .55\nDấu hiệu Trendelenburg. . . .. . . . . . . . . . .56\nDấu hiệu ngăn kéo trước . . . . . . . . ..2\nSự khác biệt độ dài 2 chân thực sự. . . . . .57\nNghiệm pháp Apley. . . . . . . . . . . . .3\nBàn tay gió thổi . . . . . . . . . . . . . 58\nNghiệm pháp cào lưng Apley. . . . . . . . . 4\nDấu hiệu chữ V . . . . . . . . . . . . . 59\nBất bình đẳng chiều dài. . . . . . . . . . . 5\nVẹo ngoài. . . . . . . . 

### III. Xử lý các chunks dữ liệu và vector hóa

In [ ]:
separators = [
    "\n\n",
    "\n",
    " ",
    ".",
    ",",
    "\u200b",  # Zero-width space (Dấu cách không chiều rộng)
    "\uff0c",  # Fullwidth comma (Dấu phẩy kiểu fullwidth)
    "\u3001",  # Ideographic comma (Dấu phẩy tượng hình)
    "\uff0e",  # Fullwidth full stop (Dấu chấm kiểu fullwidth)
    "\u3002",  # Ideographic full stop (Dấu chấm tượng hình)
    "",
]
chunk_size = 500
chunk_overlap = 50

def word_count(text):
    return len(text.split())

In [ ]:
# Bộ chia dữ liệu
document_splitter = RecursiveCharacterTextSplitter(
    separators = separators,
    chunk_size = chunk_size,
    chunk_overlap = chunk_overlap,
    length_function = word_count,
    is_separator_regex = False
)

In [52]:
chunks = document_splitter.split_documents(documents)
chunks

[Document(metadata={'source': 'data\\cleaned_txt_files\\co_che_trieu_chung_hoc.txt'}, page_content='Cơ Chế\nTriệu Chứng Học\nCơ Chế\nTriệu Chứng Học\nBiên Dịch: Nhóm Chia Sẻ Ca Lâm Sàng\nFacebook: https://www.facebook.com/calamsanghay/\nMark Dennis\nGiám Đốc Bệnh ViệnWollongong, Australia\nWilliam Talbot Bowen\nTrưởng Khoa Cấp Cứu\nBệnh Viện Đại Học Y Khoa\nBang Louisiana, Hoa Kì\nLucy Cho\nGiám Đốc Bệnh Viện Hoàng Gia Newcastle, Úc\nMục Lục\nChương 1 Nghiệm pháp Thomas. . . . . . . . . . .54\nTriệu Chứng Cơ Xương Khớp . . . . . .1 Nghiệm pháp Tinel. . . . .. . . . . . . . . . . . . .55\nDấu hiệu Trendelenburg. . . .. . . . . . . . . . .56\nDấu hiệu ngăn kéo trước . . . . . . . . ..2\nSự khác biệt độ dài 2 chân thực sự. . . . . .57\nNghiệm pháp Apley. . . . . . . . . . . . .3\nBàn tay gió thổi . . . . . . . . . . . . . 58\nNghiệm pháp cào lưng Apley. . . . . . . . . 4\nDấu hiệu chữ V . . . . . . . . . . . . . 59\nBất bình đẳng chiều dài. . . . . . . . . . . 5\nVẹo ngoài. . . . . . . . 

#### Mô hình Embedding 

In [3]:
from langchain_community.embeddings import HuggingFaceEmbeddings

model_name = "sentence-transformers/all-MiniLM-L6-v2"
# model_kwargs = {'device': 'cpu'}
model_kwargs = {'device': 'cuda'}
encode_kwargs = {'normalize_embeddings': False} # Chuẩn hóa vector = True sẽ limit length vector = 1
embedding_model = HuggingFaceEmbeddings(
        model_name=model_name,
        model_kwargs=model_kwargs,
        encode_kwargs=encode_kwargs,
    )

C:\Users\ADMIN\AppData\Local\Temp\ipykernel_12960\574808883.py:7: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embedding_model = HuggingFaceEmbeddings(
c:\Users\ADMIN\OneDrive\Documents\Btap_Code\VisualStudioCode\Python\TLCN_HealthChatbot\.venv\Lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


#### Test model embedding

In [66]:
embedded_txt = embedding_model.embed_query('Các triệu chứng của bệnh sốt xuất huyết')
embedded_txt

[-0.15472908318042755,
 0.045272380113601685,
 -0.013516238890588284,
 -0.0018604343058541417,
 -0.0011146318865939975,
 0.027056843042373657,
 0.12449567019939423,
 0.09488315880298615,
 0.012381029315292835,
 -0.06255821883678436,
 0.10982800275087357,
 -0.1193968877196312,
 -0.011329133063554764,
 -0.07560651004314423,
 -0.010105054825544357,
 -0.02762063406407833,
 -0.024316640570759773,
 0.047669459134340286,
 0.0035030220169574022,
 -0.09132391214370728,
 -0.05791659653186798,
 -0.02795218862593174,
 0.02848030999302864,
 0.03195668011903763,
 -0.06904039531946182,
 -0.051254745572805405,
 0.0013106997357681394,
 -0.03074350394308567,
 0.04525423049926758,
 -0.07892537862062454,
 0.020526308566331863,
 0.1677018254995346,
 -0.025570811703801155,
 0.014156281016767025,
 0.07861002534627914,
 -0.005160131957381964,
 0.016887027770280838,
 -0.14093191921710968,
 -0.031163878738880157,
 0.016449181362986565,
 -0.026656998321413994,
 -0.007944656535983086,
 -0.01499429065734148,
 -0.0

### IV. Cở sở dữ liệu Vector 

#### Khởi tạo Pinecone và lưu dữ liệu

In [57]:
pc = Pinecone(api_key=pinecone_api_key)
index = pc.Index('medical')

In [58]:
db = PineconeVectorStore.from_documents(documents=chunks, embedding=embedding_model, index_name="medical",
                                            namespace="docs-ute-store" )

#### Tạo lớp truy xuất dữ liệu Pinecone

In [4]:
class VectorDB:
    def __init__(self):
        self.embedding = embedding_model
        self.db = self.__build_db__()

    def __build_db__(self):
        db = PineconeVectorStore.from_existing_index(
            index_name="medical",
            namespace="docs-ute-store",
            embedding=self.embedding
        )
        return db

    def get_retriever(self,
                      search_type: str = 'similarity',
                      search_kwargs: dict = {'k': 10}):
        retriever = self.db.as_retriever(search_type=search_type, search_kwargs=search_kwargs)
        return retriever

### V. Tải mô hình và trả lời câu hỏi

#### Tải thư viện cần

In [5]:
from langchain_community.llms.ctransformers import CTransformers
from langchain.chains.retrieval_qa.base import RetrievalQA
from langchain.prompts import PromptTemplate

#### Tải mô hình đã lượng tự hóa

In [6]:
model_name = "model/llama-2-7b-chat.ggmlv3.q4_0.bin"

def load_model():
    llm = CTransformers(
        model = model_name,
        model_type = 'llama',
        max_new_token = 1024,
        temperature = 0.2,
    )
    return llm

#### Xây dựng Prompt Template và Chains cho trả lời câu hỏi

In [7]:
def create_prompt_template(template):
    prompt = PromptTemplate(template = template, input_variables = ['context', 'question'])
    return prompt

def create_qa(llm, prompt):
    llm_chain = RetrievalQA.from_chain_type(
        llm = llm,
        chain_type = 'stuff',
        retriever = VectorDB().get_retriever(),
        return_source_documents = False,
        chain_type_kwargs = {'prompt': prompt}
    )
    return llm_chain

#### Response câu trả lời của model

In [8]:
llm = load_model()

prompt_template="""
Use the following pieces of information to answer the user's question.
If you don't know the answer, just say that you don't know, don't try to make up an answer.

Context: {context}
Question: {question}

Only return the helpful answer below and nothing else.
Helpful answer:
"""

prompt = create_prompt_template(prompt_template)
qa_chain = create_qa(llm, prompt)

In [ ]:
question = "What are the symptoms of pneumonia?"
output = qa_chain.invoke({'query': question})
print(output)